In [28]:
import numpy as np
import pandas as pd
import os
import cv2
from sklearn.model_selection import train_test_split
from keras.utils import to_categorical
from keras.models import Model
from keras.layers import Dense, GlobalAveragePooling2D, Dropout
from keras.applications.vgg16 import VGG16
from keras.applications.inception_v3 import InceptionV3

In [29]:
# Load and preprocess the data
data_path = '/content/sample_data/brain tumour'
classes = ['no', 'yes']
img_size = 224

X = []
Y = []
for c in classes:
    path = os.path.join(data_path, c)
    class_num = classes.index(c)
    for img in os.listdir(path):
        img_arr = cv2.imread(os.path.join(path, img), cv2.IMREAD_COLOR)
        img_arr = cv2.resize(img_arr, (img_size, img_size))
        X.append(img_arr)
        Y.append(class_num)

X = np.array(X)
Y = np.array(Y)
Y = to_categorical(Y, num_classes=len(classes))

In [30]:
# Split the data into training and validation sets
X_train, X_val, Y_train, Y_val = train_test_split(X, Y, test_size=0.2, random_state=42)


In [31]:
# Load the pre-trained VGG16 and InceptionV3 models
base_model1 = VGG16(weights='imagenet', include_top=False, input_shape=(img_size, img_size, 3))
base_model2 = InceptionV3(weights='imagenet', include_top=False, input_shape=(img_size, img_size, 3))


In [32]:
# Create the hybrid model
x1 = base_model1.output
x1 = GlobalAveragePooling2D()(x1)
x1 = Dense(1024, activation='relu')(x1)
x1 = Dropout(0.5)(x1)
predictions1 = Dense(len(classes), activation='softmax')(x1)

x2 = base_model2.output
x2 = GlobalAveragePooling2D()(x2)
x2 = Dense(1024, activation='relu')(x2)
x2 = Dropout(0.5)(x2)
predictions2 = Dense(len(classes), activation='softmax')(x2)

model = Model(inputs=[base_model1.input, base_model2.input], outputs=[predictions1, predictions2])


In [33]:
# Freeze the layers in the pre-trained models
for layer in base_model1.layers:
    layer.trainable = False

for layer in base_model2.layers:
    layer.trainable = False


In [36]:
# Compile the model
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy','accuracy'])

In [ ]:
# Train the model
batch_size = 32
epochs = 30

history = model.fit([X_train, X_train], [Y_train, Y_train], batch_size=batch_size, epochs=epochs, verbose=1, validation_data=([X_val, X_val], [Y_val, Y_val]))

Epoch 1/30
7/7 ━━━━━━━━━━━━━━━━━━━━ 213s 25s/step - dense_13_accuracy: 0.5236 - dense_13_loss: 5.7642 - dense_15_accuracy: 0.5085 - dense_15_loss: 65.5049 - loss: 72.0636 - val_dense_13_accuracy: 0.4314 - val_dense_13_loss: 3.0990 - val_dense_15_accuracy: 0.3922 - val_dense_15_loss: 33.3858 - val_loss: 37.6369
Epoch 2/30
7/7 ━━━━━━━━━━━━━━━━━━━━ 199s 25s/step - dense_13_accuracy: 0.7153 - dense_13_loss: 1.5707 - dense_15_accuracy: 0.5964 - dense_15_loss: 20.0788 - loss: 21.6360 - val_dense_13_accuracy: 0.8627 - val_dense_13_loss: 0.9248 - val_dense_15_accuracy: 0.6863 - val_dense_15_loss: 7.2131 - val_loss: 8.0070
Epoch 3/30
7/7 ━━━━━━━━━━━━━━━━━━━━ 202s 25s/step - dense_13_accuracy: 0.8302 - dense_13_loss: 0.9018 - dense_15_accuracy: 0.7002 - dense_15_loss: 11.5050 - loss: 12.4664 - val_dense_13_accuracy: 0.8627 - val_dense_13_loss: 0.5806 - val_dense_15_accuracy: 0.8235 - val_dense_15_loss: 3.8812 - val_loss: 4.1582
Epoch 4/30
7/7 ━━━━━━━━━━━━━━━━━━━━ 161s 24s/step - dense_13_accurac

In [38]:
model.summary()

Model: "functional_3"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)              ┃ Output Shape           ┃        Param # ┃ Connected to           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer_5             │ (None, 224, 224, 3)    │              0 │ -                      │
│ (InputLayer)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_188 (Conv2D)       │ (None, 111, 111, 32)   │            864 │ input_layer_5[0][0]    │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_188   │ (None, 111, 111, 32)   │             96 │ conv2d_188[0][0]       │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_188            │ (None, 111, 111, 32)   │              0 │ batch_normalization_1… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_189 (Conv2D)       │ (None, 109, 109, 32)   │          9,216 │ activation_188[0][0]   │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_189   │ (None, 109, 109, 32)   │             96 │ conv2d_189[0][0]       │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_189            │ (None, 109, 109, 32)   │              0 │ batch_normalization_1… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_190 (Conv2D)       │ (None, 109, 109, 64)   │         18,432 │ activation_189[0][0]   │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_190   │ (None, 109, 109, 64)   │            192 │ conv2d_190[0][0]       │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_190            │ (None, 109, 109, 64)   │              0 │ batch_normalization_1… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ max_pooling2d_8           │ (None, 54, 54, 64)     │              0 │ activation_190[0][0]   │
│ (MaxPooling2D)            │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_191 (Conv2D)       │ (None, 54, 54, 80)     │          5,120 │ max_pooling2d_8[0][0]  │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_191   │ (None, 54, 54, 80)     │            240 │ conv2d_191[0][0]       │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_191            │ (None, 54, 54, 80)     │              0 │ batch_normalization_1… │
│ (Activation)              │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_192 (Conv2D)  

 Total params: 44,400,238 (169.37 MB)

 Trainable params: 2,627,588 (10.02 MB)

 Non-trainable params: 36,517,472 (139.30 MB)

 Optimizer params: 5,255,178 (20.05 MB)

In [39]:
from keras.utils import plot_model

plot_model(model, to_file='model.png', show_shapes=True)


dot: graph is too large for cairo-renderer bitmaps. Scaling by 0.61145 to fit



In [40]:
score = model.evaluate([ X_val,  X_val], [Y_val, Y_val], verbose=0)
print('Validation loss:', score[0])
print('Validation accuracy:', score[1])



Validation loss: 1.1831672191619873
Validation accuracy: 0.7517518401145935


In [41]:
# Save the model
model.save('brain_tumor_detection.h5')
